# Кластеризация и характеристика обращений клиентов

In [1]:
import os
import re
import json
import warnings
import logging

import pandas as pd
import numpy as np
import plotly.express as px
import plotly.io as pio

import pymssql
import transformers
import torch

from tqdm.auto import tqdm
from sklearn.metrics import silhouette_score, davies_bouldin_score
from sklearn.manifold import TSNE
from sklearn.cluster import KMeans
from torch.utils.data import DataLoader
from transformers import AutoTokenizer, AutoModel
from openai import OpenAI
from bert_score import score

warnings.filterwarnings("ignore", category=UserWarning)
pd.set_option('display.max_colwidth', None)
transformers.tokenization_utils.logger.setLevel(logging.ERROR)
transformers.configuration_utils.logger.setLevel(logging.ERROR)
transformers.modeling_utils.logger.setLevel(logging.ERROR)
pio.renderers.default = "notebook_connected"

SEED = 654321

In [2]:
def ms_sql_con():
    sql_name = 'voice_ai'
    sql_server = '10.2.4.124'
    sql_login = 'ICECORP\\1c_sql'

    with open('sql.pass','r') as file:
        sql_pass = file.read().replace('\n', '')
        file.close()

    return pymssql.connect(
            server = sql_server,
            user = sql_login,
            password = sql_pass,
            database = sql_name,
            tds_version=r'7.0',
            charset='cp1251'
    )

In [3]:
def read_sql(query):
    return pd.read_sql_query(query, con=ms_sql_con(), parse_dates=None)

In [4]:
calls_query = '''
SELECT TOP 5 *
FROM calls
WHERE CAST(call_date AS DATE) BETWEEN '2024-02-15' AND '2024-02-15';
'''

In [5]:
calls = read_sql(calls_query)
calls

id           call_date     ak   miko    mrm  incoming  \
0  9496315 2024-02-15 06:51:51   True  False   True     False   
1  9496316 2024-02-15 06:56:08   True  False   True     False   
2  9496317 2024-02-15 07:00:13  False   True  False     False   
3  9496314 2024-02-15 06:51:07  False   True  False     False   
4  9496313 2024-02-15 06:51:07  False   True  False     False   

                                                                                                                                                                                                                                                          linkedid  \
0  1707969110.24765442                                                                                                                                                                                                                                               
1  1707969368.24765452                                                                                                                                                                                                                                               
2  1707969611.16732185                                                                                                                                                                                                                                               
3  1707969066.16732153                                                                                                                                                                                                                                               
4  1707969066.16732153                                                                                                                                                                                                                                               

                                                                                                                                                                                                                                                              oper  \
0  МРМ                                                                                                                                                                                                                                                               
1  МРМ                                                                                                                                                                                                                                                               
2  Оператор_015                                                                                                                                                                                                                                                      
3  ФедоренкоОА_ОТК_удаленка                                                                                                                                                                                                                                          
4  ФедоренкоОА_ОТК_удаленка                                                                                                                                                                                                                                          

                                                                                                                                                                                                                                                         base_name  \
0  1C_Service_NNOV                                                                                                                                                                                               

In [7]:
tr_query = '''
SELECT TOP 5 *
FROM transcribations
WHERE CAST(record_date AS DATE) BETWEEN '2024-02-15' AND '2024-02-15';
'''

In [8]:
transcribations = read_sql(tr_query)
transcribations.T

0  \
transcribation_date                                         2024-02-15 04:35:02   
date_y                                                                     None   
date_m                                                                     None   
date_d                                                                     None   
side                                                                       True   
text                 а скади куда зайдя с каких часов а не работает после будет   
start                                                                    136.56   
audio_file_name                         in_5015_2024-02-15-04-20-52rxtx-out.wav   
conf                                                                   0.695704   
end_time                                                                 140.97   
sentiment                                                                  None   
sentiment_pos                                                              None   
sentiment_neg                                                              None   
ID                                                                    173033639   
linkedid                                                    1707960050.16732024   
dst                                                                        main   
record_date                                                 2024-02-15 04:20:52   
source_id                                                                     1   
src                                                                        5015   
cpu_id                                                                        1   
duration                                                                 182.38   
file_size                                                               2918124   
queue_date                                                  2024-02-15 04:33:56   
model                                                                         0   

                                                                            1  \
transcribation_date                                       2024-02-15 04:35:02   
date_y                                                                   None   
date_m                                                                   None   
date_d                                                                   None   
side                                                                     True   
text                 а а это самая подождите а вы не можете сказать стоимость   
start                                                                  147.99   
audio_file_name                       in_5015_2024-02-15-04-20-52rxtx-out.wav   
conf                                                                 0.984123   
end_time                                                               152.85   
sentiment                                                                None   
sentiment_pos                                                            None   
sentiment_neg                                                            None   
ID                                                                  173033640   
linkedid                                                  1707960050.16732024   
dst                                                                      main   
record_date                                               2024-02-15 04:20:52   
source_id                                                                   1   
src                                                                      5015   
cpu_id                                                                      1   
duration                                                               182.38   
file_size                                                             2918124   
queue_date                                                2024-02-15 04:33:56   
model                                                     

In [9]:
query = '''
SELECT DISTINCT
       start,
       record_date,
       linkedid,
       audio_file_name,
       model,
       text,
       side,
       src,
       dst
FROM transcribations
WHERE linkedid IN (SELECT DISTINCT
                          linkedid
                   FROM transcribations
                   WHERE CAST(record_date AS DATE) BETWEEN '2024-02-07' AND '2024-02-15'
                       AND model=1)
    AND ((side='True' AND LEN(src)=4 AND dst NOT LIKE '[0-9][0-9][0-9][0-9]')
         OR (side='False' AND LEN(src)>4 AND dst LIKE '[0-9][0-9][0-9][0-9]')
         OR (side='True' AND LEN(src)>4 AND LEN(dst)>4))
    AND text IS NOT NULL AND text <> ''
ORDER BY start;
'''

In [19]:
df = read_sql(query)
df = df.drop(columns=['start']).drop_duplicates()
df.sample(5)

record_date             linkedid  \
21150  2024-02-08 12:45:37  1707385535.16510045   
112292 2024-02-08 16:28:33  1707398913.16522791   
36945  2024-02-08 15:25:19  1707395118.16519355   
79015  2024-02-13 11:47:44  1707814062.16671718   
1401   2024-02-09 21:13:11  1707502390.16564456   

                                     audio_file_name  model  \
21150        in_5056_2024-02-08-12-45-37rxtx-out.wav      1   
112292       in_5023_2024-02-08-16-28-33rxtx-out.wav      1   
36945        in_5089_2024-02-08-15-25-19rxtx-out.wav      0   
79015   in_8127006533_2024-02-13-11-47-44rxtx-in.wav      1   
1401         in_5046_2024-02-09-21-13-11rxtx-out.wav      1   

                                                                                                   text  \
21150                                                    Да, работа выполнена. Вроде все пока работает.   
112292                                                                Я уже всех предупредила, сказала.   
36945                                                                 ну я нашёл вот этот самый в почте   
79015                                                                                               Да.   
1401     да хотя бы мастера по ремонту телевизора домой ремонт дома хотел там отмечал в 12 до 2 samsung   

         side         src   dst  
21150    True        5056  main  
112292   True        5023  main  
36945    True        5089  main  
79015   False  8127006533  5023  
1401     True        5046  main

In [21]:
df.to_csv('calls_transcripts.csv', index=False)
df = pd.read_csv(
    'calls_transcripts.csv',
    parse_dates=[0],
    dtype={'linkedid': 'object'}
)

In [22]:
summarized = df.groupby(
    [
       'linkedid',
       'audio_file_name',
       'record_date',
       'model',
       'side',
       'src',
       'dst'
    ],
    as_index=False
).agg({'text': ' '.join})

In [23]:
summarized['text'] = summarized['text'].str.lower().replace(
    'продолжение следует',
    '',
    regex=True
)
summarized['text'] = summarized['text'].str.lower().replace(
    r'\.{2,}',
    '',
    regex=True
)

In [24]:
summarized['text_length'] = summarized['text'].apply(len)
summarized = summarized[summarized['text_length'] >= 50]
summarized = summarized.sort_values(by=['linkedid', 'record_date']).drop_duplicates(subset='linkedid').reset_index(drop=True)

In [53]:
summarized.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 8103 entries, 0 to 8102
Data columns (total 9 columns):
 #   Column           Non-Null Count  Dtype         
---  ------           --------------  -----         
 0   linkedid         8103 non-null   object        
 1   audio_file_name  8103 non-null   object        
 2   record_date      8103 non-null   datetime64[ns]
 3   model            8103 non-null   int64         
 4   side             8103 non-null   bool          
 5   src              8103 non-null   object        
 6   dst              8103 non-null   object        
 7   text             8103 non-null   object        
 8   text_length      8103 non-null   int64         
dtypes: bool(1), datetime64[ns](1), int64(2), object(5)
memory usage: 514.5+ KB


In [54]:
summarized.to_csv('summarized_transcripts.csv', index=False)
summarized = pd.read_csv(
    'summarized_transcripts.csv',
    parse_dates=[2],
    dtype={'linkedid': 'object'}
)

In [55]:
summary = pd.DataFrame()
summary[['linkedid', 'text']] = summarized[['linkedid', 'text']]

In [56]:
client = OpenAI(api_key=os.environ["OPENAI_API_KEY"])

def generate_summary(text):
    response = client.chat.completions.create(
        model="gpt-3.5-turbo-1106",
        seed=SEED,
        messages=[
            {"role": "system", "content": "Выдели из полученного текста только важные для сервисного центра по ремонту бытовой техники, куда обращается клиент данным текстом, фразы с вопросами, запросами клиента, только когда он хочет что-то выяснить, обращается по поводу какой-то проблемы, заявляет о ней. НЕ ВЫВОДИ НЕНУЖНЫЕ ДЕТАЛИ, такие как адреса, время, телефоны, номера и тому подобное. ПЕРЕЧИСЛЕННОЕ - ЛИШНЯЯ ИНФОРМАЦИЯ. Твоя конечная цель - донести до руководства, с какими запросами от клиентов в первую очередь сталкиваются сотрудники компании. Выводи одной строкой, но состоящей из ОТДЕЛЬНЫХ уникальных предложений, каждое из которых будет содержать весь необходимый контекст, чтобы взглянув на предложение, можно было понять, о чём речь, не видя остальных прердложений. Для этого сначала перефразируй каждую фразу в отдельное предложение так, чтобы оно выглядело понятным и самодостаточным, но используй только исходную смысловую информацию во всём тексте, не придумывай НИКАКУЮ свою. ТОЛЬКО если ты не можешь выделить требуемую информацию, вместо самостоятельно генерируемого ответа выводи: Нет ключевой информации."},
            {"role": "user", "content": "але але да але але да да да сегодня бедняки да подъезжайте нет проблем да да да но вы поняли что у нас каждая дверь морозильной камеры или сама русловая уплотнительная резинка нужда нет ну в этот самый раз и фрагменты и у неё там ну вы же только бутылку хотите посмотреть ничего не делая как я вам могу скинуть размеры я в интернете смотрела да хорошо хорошо проще."},
            {"role": "assistant", "content": "У нас проблема с уплотнительной резинкой или дверью морозильной камеры. Вы только бутылку хотите посмотреть, как я могу вам передать размеры?"},
            {"role": "user", "content": text}
        ]
    )
    return response.choices[0].message.content

def compute_scores(row):
    P, R, F1 = score(
        [row['result']],
        [row['text']],
        lang="ru"
    )
    return pd.Series([P.item(), R.item(), F1.item()])

In [59]:
summary['result'] = summary['text'].apply(generate_summary)
summary[[
    'precision',
    'recall',
    'f1'
]] = summary.apply(compute_scores, axis=1)
summary[['text', 'result']].sample(5)

text  \
1722                                                                                                                                                                                                                                                     да, слушаю вас.  спасибо вам большое.  ожидаем, спасибо.   
1454                                                                                    здравствуйте. это у меня пропущенные вызовы.  а, ясно.  да-да, я слышу. а как с мастером связаться?  хорошо. вчера меня звонок ваш застал на улице.  на улице разговаривать неудобно, морозно.  а потом  хорошо. спасибо.   
1489                                                                                                                                                                                                                      але сейчас подожди нет деталей ори сиз о господи борисе что за ури сис нет документацию   
2355  але да да да оба кока сейчас минут через двадцать просто у меня плену не не не сказал он мне я не знаю от кука наличных я думала вот расчёт там будет те кока не знаете сколько стоит чтоб мне наличными а выдох не знаете сколько стоит а у мастеров ну ладно хорошо пускай приходят хорошо да все давайте   
247                                                           алло джеки о только лишь тем перевернём да так от недели до двадцати одного дня поняла я очень надеюсь что придёт раньше потому что двадцать один день без холодильника это прям совсем печально хорошо тогда жду вашего звонка спасибо до свидания   

                                                                                                                   result  
1722                                                                                             Нет ключевой информации.  
1454  Как я могу связаться с мастером? Вчера меня ваш звонок застал на улице, а разговаривать на улице неудобно, морозно.  
1489                                                                                             Нет ключевой информации.  
2355                                                                                             Нет ключевой информации.  
247                 Надеюсь, что ремонт придёт раньше, потому что 21 день без холодильника - печально. Жду вашего звонка.

In [60]:
summary.to_csv('summary.csv', index=False)
summary = pd.read_csv(
    'summary.csv',
    dtype={'linkedid': 'object'}
)

In [61]:
def process_text(text):
    text = text.replace('"', '')
    text = text.replace('\n', ' ')
    text = re.sub(r'\b\d\.\s*', '', text)
    text = re.sub(r'(?<=[\.?])\s+', '', text)
    text = re.sub(r'(?<!\s)-\s', '', text)
    fragments = re.split(r'(?<=[\.?])', text)
    fragments = [frag.lstrip() for frag in fragments if frag.strip()]
    return fragments

In [62]:
summary = summary[~summary.result.str.contains(
    'нет ключевой информации|не удалось выделить ключевую информацию|никакого разговора не состоялось',
    case=False
)].reset_index(drop=True)

fragments = summary.result.apply(process_text)
clean = pd.DataFrame({
    'linkedid': summary.linkedid.repeat(fragments.apply(len)).values,
    'text': [frag for list in fragments for frag in list]
})
clean = clean[~clean.text.str.contains(
    'адрес|город|метро|дом|квартир|подъезд|домофон|этаж|мой телефон|наш телефон|мой номер|номер телефона|номер заявки|номер заказа|телефон для связи|контактный номер|контактный телефон|спасибо|до свидания',
    case=False
)]
clean = clean[clean.text.str.contains(
    r'[а-яА-ЯёЁ]',
    regex=True
)].reset_index(drop=True)

clean['text'].to_frame().sample(10)

text
1049                                                                                                Запчастей нет, техника примерно 2009 года, может быть лучше сдать и купить новую.
5889                                                                                                                                     Шланг, подключенный к машине, капает сверху.
3644                                                                                                   Мне нужно поставить в межкомнатную дверь замочек, который закрывается на ключ.
3230                                                                                                                       Машина стоит 30, но все равно больше десятки будет стоить?
2069                                                                                                                                                          Прошу магнитный сайдер.
2791  У меня проблемы с телевизором, когда я выключаю свет, телевизор тоже выключается, у меня приставка Харпер, работает только через каждую секунду, зовите мастера, нужен сегодня.
7894                                                                                                                                                               Сколько это стоит?
3335                                                  Мастер сообщает клиенту, что демонтаж для ремонта не будет бесплатным, но ранее мы обговаривали, что он должен быть бесплатным.
4663                                                                                                                                         Может проще просто купить новую духовку?
366                                                                                                                                                         Сможете подъехать завтра?

In [63]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
tokenizer = AutoTokenizer.from_pretrained('cointegrated/rubert-tiny2')
model = AutoModel.from_pretrained('cointegrated/rubert-tiny2').to(device)

def ave_pool(lhs, mask):
    last_hidden_state = lhs.masked_fill(~mask[..., None].bool(), 0.0)
    return last_hidden_state.sum(dim=1) / mask.sum(dim=1)[..., None]

def get_embeddings(df):
    sentences = df['text'].astype(str).tolist()

    bs = 512
    loader = DataLoader(
        sentences,
        batch_size=bs,
        shuffle=False
    )
    embeddings = []
    
    for batch in tqdm(loader, desc='Processing batches'):
        input = tokenizer(
            batch,
            padding=True,
            truncation=True,
            return_tensors='pt'
        ).to(device)

        with torch.no_grad():
            output = model(**input).last_hidden_state

        attention_mask = input.attention_mask

        embedding = ave_pool(output, attention_mask).cpu().numpy()
        embeddings.extend(embedding)

    df['embedding'] = embeddings
    return df

In [64]:
embeddings = get_embeddings(clean)
embeddings.tail()

Processing batches:   0%|          | 0/19 [00:00<?, ?it/s]

linkedid  \
9493  1708026084.16765862   
9494  1708026084.16765862   
9495  1708026084.16765862   
9496  1708026084.16765862   
9497  1708026084.16765862   

                                                                   text  \
9493  Машина перестала работать, мотор шумел, сейчас отключена от сети.   
9494                                         Сколько стоит диагностика?   
9495                        Когда-то нужно будет договориться о визите.   
9496                   Если мотор сломался, то гарантия действует, так?   
9497                               У меня есть документы, чек и прочее.   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              embedding  
9493        [-0.4979679, -0.16442797, 0.36842173, -1.676214, 0.3559669, 0.19501455, -0.42754954, -0.94375217, 0.71071756, 0.011492193, 0.3678645, 0.45247632, 0.5550098, 0.8986785, -0.37330252, -0.6497234, 0.6455413, -0.023895614, -0.61900723, -0.79517746, -0.095056355, 0.9744611, 0.13928863, -0.26286507, 0.85038006, 0.27458072, 0.5151521, 0.019576043, -0.033802614, 0.71436477, -0.38502896, -0.09489034, -0.05438745, -0.10605653, 0.37437785, 0.58846146, 0.014951134, -0.68956316, 0.4838717, -0.12497558, 0.630146, 0.4168074, 0.34916487, -0.34569946, 0.5091611, 0.15328164, -0.37202215, 1.0042703, 0.09382937, -0.16301294, -0.34029534, 0.07011742, -0.07011939, -0.3813418, 0.17086992, -0.26923758, 0.65138745, 0.044585854, 0.032859582, -0.10529827, 0.4048554, 0.3378154, 1.0203592, -0.7453835, 0.71147454, -0.7332988, 0.2426767, 0.2388079, 0.3004897, -0.26576555, 1.1265013, 0.35250518, -0.47162372, -0.8783016, 0.40011892, -0.8526208, 0.008848876, -0.4220984, 0.15422377, 0.27740133, -0.02472756, -0.060771517, 0.085469306, 0.39651388, -0.26952672, -0.6925851, -0.99020034, 0.38377187, -0.21832691, -0.56522065, 0.94754934, -0.22286668, 0.44678244, -0.21607503, 0.8348493, 0.31849736, 0.42448932, 0.19199519, 0.17139351, -0.1333192, ...]  
9494                [-0.056837603, -0.12828873, -0.33625045, -1.046955, -0.742052, -0.19488113, 0.22727776, -0.24017954, -0.29870102, 0.15916987, 0.19967127, -0.38493606, 0.1942632, 1.7492805, -0.51252276, -0.2938362, 0.67394114, 0.9360674, -0.02574356, 0.30983338, -0.2890269, 0.093564965, 0.06499841, 0.41844738, 1.7331647, -0.1167899, 0.28999856, 1.002111, 1.0973669, 0.31991345, 0.6112205, 0.6071232, -0.58056813, -0.09902742, 0.20809667, 0.2317399, 0.8121771, -0.66393685, -0.33162472, -0.050684024, 0.52022207, -0.4664117, 0.00070955855, -0.48104763, 0.35467634, -0.38893127, -0.2684473, -0.64813644, 0.8216538, 0.57753295, 0.7762627, -0.13106127, 0.126467, -0.803066, 0.31932488, 0.020890161, 0.9325392, -0.012108277, -0.17315097, 0.13772224, 0.5116455, 0.6035383, -0.5713238, -0.07231391, 0.70880765, -0.32310212, 0.19457988, 0.059459537, 0.008304007, 0.812063, -0.33621076, 0.032670736, -0.10099611

In [65]:
embeddings.to_pickle('embeddings.pkl')
embeddings = pd.read_pickle(
    'embeddings.pkl'
)

In [66]:
matrix = np.stack(embeddings.embedding.values)

best_silhouette_score = -1
best_db_index = np.inf
best_count = None
silhouette_scores = []
db_indexes = []
cluster_sizes_list = []

for count in range(4, 21):
    clusterer = KMeans(
        n_clusters=count,
        max_iter=100,
        init='random',
        n_init=10,
        random_state=SEED,
        algorithm='lloyd'
    )
    clusterer.fit(matrix)
    labels = clusterer.labels_

    cluster_sizes = np.bincount(labels[labels >= 0])
    cluster_sizes_list.append((count, cluster_sizes))
    
    if len(set(labels)) > 1:
        silhouette = silhouette_score(matrix, labels)
        db_index = davies_bouldin_score(matrix, labels)
        
        silhouette_scores.append((count, silhouette))
        db_indexes.append((count, db_index))
        
        if silhouette > best_silhouette_score:
            best_silhouette_score = silhouette
            best_count = count
        
        if db_index < best_db_index:
            best_db_index = db_index
            best_count_db = count

for count, cluster_sizes in cluster_sizes_list:
    print(f"Количество кластеров={count}, размеры кластеров: {cluster_sizes}")

print(
    "Лучшее количество кластеров по силуэту:",
    best_count,
    "с оценкой силуэта:",
    best_silhouette_score
)
print(
    "Лучшее количество кластеров по Davies-Bouldin:",
    best_count_db,
    "с индексом Davies-Bouldin:",
    best_db_index
)

Количество кластеров=4, размеры кластеров: [3009 2525  832 3132]
Количество кластеров=5, размеры кластеров: [2624 2046 2189 1915  724]
Количество кластеров=6, размеры кластеров: [2053  716 1632 1823 2128 1146]
Количество кластеров=7, размеры кластеров: [1148 1550 1226  663 1948 1699 1264]
Количество кластеров=8, размеры кластеров: [ 786  651 1781 1260 1172 1188 1084 1576]
Количество кластеров=9, размеры кластеров: [ 551 1345  963 1126  898 1716 1171  763  965]
Количество кластеров=10, размеры кластеров: [1123 1216 1195  524  894 1193  867  983  751  752]
Количество кластеров=11, размеры кластеров: [ 670  977  843 1183  642  941  892  557 1001 1085  707]
Количество кластеров=12, размеры кластеров: [1007  384  515  768 1054  633  538  709 1079 1074  985  752]
Количество кластеров=13, размеры кластеров: [ 671  785  483  979  728  741  884  893  493  967  369  475 1030]
Количество кластеров=14, размеры кластеров: [906 810 890 924 505 507 452 352 719 392 607 762 728 944]
Количество кластеро

In [67]:
def generate_topics(df, col, matrix, n_clusters, rev_per_cluster):
    messages = [
        {"role": "system", "content": "Ты - профессиональный маркетолог с многолетним стажем. Ты специализируешься на выявлении и характеризации ключевых особенностей взаимодействия пользователей, клиентов с продуктами компаний, бизнесом. Я готов заплатить тебе за хорошее правильное решение до 200$ в зависимости от его качества. Далее представлены фрагменты диалогов клиентов с сервисным центром по ремонту бытовой техники. Эти фрагменты уже разделены на несколько указанных кластеров. Сформулируй описание, название для каждого кластера так, чтобы легко было понятно, что его выделяет, характеризует среди остальных кластеров. Ответ дай в виде подобной JSON структуры, только с двойными кавычками: {'Кластер 0': 'Название 0', 'Кластер 1': 'Название 1'} и так далее."}
    ]
    message = {"role": "user", "content":""}

    tsne = TSNE(random_state=SEED)
    vis_dims2 = tsne.fit_transform(matrix)

    for i in range(n_clusters):
        cluster_df = df[df[col] == i].reset_index(drop=True)

        cluster_center = vis_dims2[cluster_df.index].mean(axis=0)

        distances = np.sqrt(((vis_dims2[cluster_df.index] - cluster_center)**2).sum(axis=1))

        closest_indices = distances.argsort()[:rev_per_cluster]

        closest_reviews = cluster_df.iloc[closest_indices].text

        reviews = "\n ".join(
            closest_reviews.values
        )
        message["content"] += f"\n Кластер {i}: {reviews} "
    
    messages.append(message)
    
    response = client.chat.completions.create(
        model="gpt-3.5-turbo-1106",
        messages=messages
    )
    topics_json = response.choices[0].message.content

    topics_dict = json.loads(topics_json)
    return topics_dict

In [68]:
general_clusterer = KMeans(
    n_clusters=4,
    max_iter=100,
    init='random',
    n_init=10,
    random_state=SEED,
    algorithm='lloyd'
)
detail_clusterer = KMeans(
    n_clusters=17,
    max_iter=100,
    init='random',
    n_init=10,
    random_state=SEED,
    algorithm='lloyd'
)
general_clusterer.fit(matrix)
detail_clusterer.fit(matrix)

general_labels = general_clusterer.labels_
detail_labels = detail_clusterer.labels_

embeddings['general_cluster'] = general_labels
embeddings['detail_cluster'] = detail_labels
embeddings['edited_cluster'] = embeddings['detail_cluster'].replace(
    {10: 0, 3: 7, 4: 13, 5: 13, 15: 13}
)

In [69]:
embeddings.to_pickle('clustered_transcripts.pkl')
embeddings = pd.read_pickle(
    'clustered_transcripts.pkl'
)

In [70]:
px.pie(
    embeddings,
    names=embeddings.general_cluster.replace({
        0: 'Проблема с оказанными услугами',
        1: 'Запрос на вызов и уточнение информации о времени и услугах',
        2: 'Запрос на цену и оценку стоимости ремонта',
        3: 'Просьба о прозвоне, уточнение деталей и контактов'
    })
).update_traces(textinfo='percent',).update_layout(
    uniformtext_minsize=36,
    uniformtext_mode='hide',
    width=2200,
    height=900,
    title=dict(
    text='Общие категории обращений',
    x=.5,
    y=.98,
    font_size=50
    ),
    legend=dict(
        font_size=30,
        y=.5,
        yanchor='middle'
    )
)

In [71]:
px.pie(
    embeddings,
    names=embeddings.edited_cluster.replace({
        0: 'Вопросы о стоимости и оплате услуг',
        1: 'Запросы о способах и возможностях связаться с мастером',
        2: 'Уточнение местоположения проблемы и требуемых услуг',
        6: 'Неудовлетворенность качеством предоставленных услуг и запросы на прекращение сотрудничества',
        7: 'Вопросы о сроках, времени и деталях визита мастера',
        8: 'Запросы о наличии запчастей и техники, а также о ценах',
        9: 'Вопросы о предоставлении квитанций, возможности отмены вызова и других дополнительных услугах',
        11: 'Запросы на перенос визита и другие подобные запросы',
        12: 'Запросы на вызов мастера и уточнение возможности ремонта',
        13: 'Уточнение проблем с бытовой техникой и запросы на ремонт',
        14: 'Запросы на быстрый приезд мастера и оказание услуг',
        16: 'Запросы на перезвон и другие коммуникационные запросы'
    })
).update_traces(textinfo='percent',).update_layout(
    uniformtext_minsize=32,
    uniformtext_mode='hide',
    width=2200,
    height=900,
    title=dict(
    text='Детальные категории обращений',
    x=.5,
    y=.98,
    font_size=50
    ),
    legend=dict(
        font_size=24,
        y=.5,
        yanchor='middle'
    )
)